In [4]:
from einops import rearrange

In [3]:
start = torch.rand(size=(4, 1, 128, 128, 128))

In [5]:
embedder = torch.nn.Conv3d(kernel_size=16, stride=16, out_channels=128, in_channels=1)

In [6]:
embedder(start).shape

torch.Size([4, 128, 8, 8, 8])

In [9]:
embedded = embedder(start)
tokens = rearrange(embedded, "b em x y z -> b (x y z) em")

In [10]:
tokens.shape

torch.Size([4, 512, 128])

In [1]:
from src.model.vit import ViT
import torch


In [2]:
model = ViT(embed_dim=128, channels=8, patch_size=16, levels=3)

In [3]:
data = [torch.rand(4, 8, 128, 128, 128), torch.rand(4, 8, 64, 64, 64), torch.rand(4, 8, 32, 32, 32)]
out = model(data)

In [7]:
[print(o.shape) for o in out]
print(2)

torch.Size([4, 8, 128, 128, 128])
torch.Size([4, 8, 64, 64, 64])
torch.Size([4, 8, 32, 32, 32])
2


In [1]:
from src.model.my_model import MyModel
from src.model.vit import DefaultViT
import torch
from src.constants import *
from src.model.baselines import SWINUNETR, UNet
import importlib

In [2]:
device= "cuda"


img = torch.rand(2, 1, 128, 128, 128).to(device)
mask = torch.rand(4, 3, 128, 128, 128).to(device)

tokens = torch.rand(size=(4, 1024, 256)).to(device)


In [3]:
model = MyModel(in_channels=1, out_channels=3, skip_transformer=False, channels=(32, 32, 32, 32, 32),transformer_channels=8, embed_dim=128).to(device)
optimizer = torch.optim.Adam(params=model.parameters(), lr=LEARNING_RATES[0])

other = UNet.to(device)

In [4]:
%%time
out = model(img)
# loss = LOSS(out, mask)
# loss.backward()
# optimizer.step()

Embed: 0.007980 seconds
ViT: 0.004902 seconds
De-Embed: 0.004544 seconds
CPU times: user 382 ms, sys: 40 ms, total: 422 ms
Wall time: 428 ms


In [5]:
%%time


UsageError: %%time is a cell magic, but the cell body is empty. Did you mean the line magic %time (single %)?


In [ ]:
encoder_layer = torch.nn.TransformerEncoderLayer(d_model=512, nhead=8, dim_feedforward=2048, dropout=0.1,
                                                    activation="gelu", layer_norm_eps=1e-5, batch_first=False, norm_first=False)

encoder_norm = torch.nn.LayerNorm(512, eps=1e-5)
encoder = torch.nn.TransformerEncoder(encoder_layer, num_layers=6, norm=encoder_norm).cuda()

In [3]:
example = torch.rand(size=(4, 1024, 512)).cuda()

In [7]:
import os

os.system("nvidia-smi")

Thu Apr 20 17:10:46 2023       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 515.86.01    Driver Version: 515.86.01    CUDA Version: 11.7     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  NVIDIA A40          On   | 00000000:3B:00.0 Off |                    0 |
|  0%   42C    P0    79W / 300W |  16707MiB / 46068MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
|   1  NVIDIA A40          On   | 00000000:5E:00.0 Off |                    0 |
|  0%   

0

In [5]:
encoder(example).shape

torch.Size([4, 1024, 512])

In [ ]:
import torch
import time

example = torch.rand(size=(4, 1, 128, 128, 128))
# Synchronize the device to ensure all operations are completed
torch.cuda.synchronize()

# Record the start time
start_time = time.time()

# Perform some operation on the GPU
out = model.vit.embedders

# Synchronize the device again to make sure the operation is completed
torch.cuda.synchronize()

# Record the end time
end_time = time.time()

# Calculate the time taken for the operation
time_elapsed = end_time - start_time
print(f'Time taken for matrix multiplication: {time_elapsed:.6f} seconds')

In [6]:
import torch

device = "cuda"

example = torch.rand(size=(4, 256, 8, 8, 8)).to(device)
conv = torch.nn.ConvTranspose3d(kernel_size=16,stride=16, in_channels=256, out_channels=8).to(device)

ts = []
for _ in range(500):
    start = torch.cuda.Event(enable_timing=True)
    end = torch.cuda.Event(enable_timing=True)

    start.record()
    out = conv(example)
    a = out[:, :, 1]
    end.record()

    torch.cuda.synchronize()
    t = start.elapsed_time(end)
    ts.append(t)
    print(a)

print(sum(ts)/len(ts))



tensor([[[[ 1.1038e-02, -1.4712e-02, -3.4136e-02,  ...,  6.1392e-03,
            1.3071e-02, -2.5770e-02],
          [-4.8705e-02,  2.9411e-02,  3.6145e-04,  ...,  3.5992e-02,
           -1.6345e-03,  1.0405e-04],
          [-2.4036e-02,  2.4462e-02,  2.0417e-02,  ...,  1.7863e-02,
           -1.8773e-02, -1.0457e-02],
          ...,
          [-2.7719e-02, -2.9493e-02,  4.9814e-04,  ...,  8.6135e-02,
           -3.6963e-02,  4.1505e-03],
          [-3.8636e-02, -2.6110e-02,  1.3793e-02,  ..., -4.7389e-02,
           -3.0724e-02,  4.4257e-03],
          [-4.9540e-02,  3.5216e-02, -4.9613e-02,  ..., -1.7905e-02,
            4.1797e-02, -1.4522e-02]],

         [[ 1.8471e-02, -1.0686e-02, -3.6591e-02,  ...,  2.1991e-02,
            2.6978e-02, -4.7535e-02],
          [ 1.1200e-02,  2.0486e-02, -3.7615e-02,  ..., -5.4221e-02,
            1.7861e-02, -3.1778e-02],
          [ 7.3289e-03, -1.1145e-02, -1.3223e-02,  ...,  4.7068e-02,
            3.9046e-03, -1.1351e-02],
          ...,
     